In [1]:
# load function
%run buffers_intersections_search_function.ipynb

In [2]:
# import packages
import geopandas
import pandas as pd
import numpy as np
import matplotlib.colors as colors

In [3]:
# user defined buffer radius in meters
buffer_size = 100

# create GeoDataFrame from the shape file
gdf = geopandas.read_file("SAO_LUIZ_DO_NORTE/CER.2020.SAO_LUIZ_DO_NORTE.GO.5220157.V.shp")

# extract only areas of primary forest class
forest_dataframe = gdf.loc[gdf["CLASSE"] == "VEGETACAO_NATURAL_PRIMARIA"]

# necessary manipulations to prepare data for processing
forest_dataframe = forest_dataframe.sort_values(by="AREA_KM", ascending=False)
forest_dataframe = forest_dataframe.reset_index()
forest_dataframe = forest_dataframe.drop(columns="index")
forest_dataframe = forest_dataframe.to_crs(crs=5641)
forest_dataframe["buffer"] = forest_dataframe["geometry"].buffer(buffer_size)
forest_dataframe.crs = "EPSG:4674"
forest_dataframe.head()

CLASSE  VALUE CODIGO    AREA_KM  Shape_Leng  \
0  VEGETACAO_NATURAL_PRIMARIA      1  1.1.1  13.853803    0.931273   
1  VEGETACAO_NATURAL_PRIMARIA      1  1.1.1  13.034474    0.843410   
2  VEGETACAO_NATURAL_PRIMARIA      1  1.1.1  11.863100    0.798866   
3  VEGETACAO_NATURAL_PRIMARIA      1  1.1.1   5.071271    0.572747   
4  VEGETACAO_NATURAL_PRIMARIA      1  1.1.1   4.767194    0.418692   

   Shape_Area                                           geometry  \
0    0.001164  POLYGON ((4319665.78966 8339070.69931, 4319665...   
1    0.001095  POLYGON ((4309763.30151 8340392.08808, 4309859...   
2    0.000997  POLYGON ((4312817.10855 8327291.37288, 4312817...   
3    0.000426  POLYGON ((4290288.55170 8327724.10266, 4290288...   
4    0.000401  POLYGON ((4290378.66592 8331060.60371, 4290389...   

                                              buffer  
0  POLYGON ((4315000.526 8334572.056, 4314999.253...  
1  POLYGON ((4302805.069 8337835.312, 4302806.465...  
2  POLYGON ((4306769.569 8325663.327, 4306769.569...  
3  POLYGON ((4290128.475 8326138.539, 4290127.727...  
4  POLYGON ((4289828.617 8330494.449, 4289827.346...

In [4]:
buffers = forest_dataframe.loc[:, "buffer"]
polygons = forest_dataframe.loc[:, "geometry"]
types = pd.DataFrame(np.arange(0, 330), columns = ["geo_type"])
types["geo_type"] = "polygon"
forest = geopandas.GeoDataFrame(crs='epsg:5641', geometry=buffers)
forest.insert(1, value=types, column ="geo_type")
forest.insert(2, value=polygons, column ="polygon")
forest["geo_type"].value_counts()
#forest.plot()
forest.head()

geometry geo_type  \
0  POLYGON ((4315000.526 8334572.056, 4314999.253...  polygon   
1  POLYGON ((4302805.069 8337835.312, 4302806.465...  polygon   
2  POLYGON ((4306769.569 8325663.327, 4306769.569...  polygon   
3  POLYGON ((4290128.475 8326138.539, 4290127.727...  polygon   
4  POLYGON ((4289828.617 8330494.449, 4289827.346...  polygon   

                                             polygon  
0  POLYGON ((4319665.78966 8339070.69931, 4319665...  
1  POLYGON ((4309763.30151 8340392.08808, 4309859...  
2  POLYGON ((4312817.10855 8327291.37288, 4312817...  
3  POLYGON ((4290288.55170 8327724.10266, 4290288...  
4  POLYGON ((4290378.66592 8331060.60371, 4290389...

In [5]:
result = create_geodataframe(forest)
result.info()

Intersections found:  74
<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 74 entries, 0 to 73
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype   
---  ------    --------------  -----   
 0   geometry  74 non-null     geometry
 1   geo_type  74 non-null     object  
dtypes: geometry(1), object(1)
memory usage: 1.3+ KB


In [6]:
result.value_counts("geo_type")

geo_type
polygon     51
corridor    23
dtype: int64

In [8]:
result.explore("geo_type", cmap=colors.ListedColormap(["#006400", "#ffae42"]))

In [9]:
# to save data into shapefile is needed to change crs
forest_dataframe = forest_dataframe.set_crs(5641, allow_override=True)

In [10]:
buffers = result[result["geo_type"] == "corridor"]

In [11]:
for buffer_id in range(0, buffers.shape[0]):
    
    contains = buffers.iloc[buffer_id, 0].contains(forest_dataframe.iloc[:, 6])
    
    list_of_polygons = forest_dataframe.loc[contains]["geometry"]

    gdf = geopandas.GeoDataFrame(geometry=list_of_polygons)
   
    gdf.to_file(f'corridors/buffer_{buffer_id}.shp')